In [1]:
%pwd

'/home/janderson/Documentos/challenge-artificial-intelligence/research'

In [2]:
import os 
os.chdir("../")

In [3]:
import statistics
import fitz

def extract_sections_from_pdf(pdf_path, bold_boost=1.05):

    doc = fitz.open(pdf_path)

    # 1) Descobrir tamanho "corpo" (mediana de tamanhos não-bold)
    body_sizes = []
    for page in doc:
        for b in page.get_text("dict")["blocks"]:
            print(b)
    
    

    # sections = []
    # current_title = None
    # current_buf = []

    # def flush_section():
    #     nonlocal current_title, current_buf
    #     if current_title is not None:
    #         sections.append({
    #             "title": current_title.strip(),
    #             "content": "\n".join(current_buf).strip()
    #         })
    #         current_title, current_buf = None, []

    # # 2) Percorrer spans, juntando títulos e conteúdos
    # for page in doc:
    #     for b in page.get_text("dict")["blocks"]:
    #         for ln in b.get("lines", []):
    #             # um "título" pode vir em vários spans; vamos colá-los
    #             line_title_parts = []
    #             line_has_title = False

    #             for sp in ln.get("spans", []):
    #                 text = sp.get("text", "")
    #                 if not text.strip():
    #                     continue

    #                 size = sp.get("size", 0.0)
    #                 font = sp.get("font", "")
    #                 flags = sp.get("flags", 0)
    #                 is_bold = bool(flags & 2) or ("Bold" in font)

    #                 # Heurística de título: bold E maior que o corpo
    #                 if is_bold and (size >= body_size * bold_boost):
    #                     line_title_parts.append(text)
    #                     line_has_title = True
    #                 else:
    #                     # conteúdo normal: despeja qualquer título pendente e adiciona o texto
    #                     if line_has_title:
    #                         # final da linha-título
    #                         # fecha seção anterior e abre uma nova
    #                         flush_section()
    #                         current_title = "".join(line_title_parts).strip()
    #                         line_title_parts = []
    #                         line_has_title = False
    #                     current_buf.append(text)

    #             # se a linha inteira era título, fecha/abre seção aqui
    #             if line_has_title:
    #                 flush_section()
    #                 current_title = "".join(line_title_parts).strip()

    #         # quebra de bloco costuma significar parágrafo
    #         current_buf.append("")

    # # finalizar última seção
    # flush_section()

    # # limpeza: remover seções vazias e juntar quebras extras
    # cleaned = []
    # for sec in sections:
    #     content = "\n".join([ln for ln in sec["content"].splitlines() if ln.strip() != ""]).strip()
    #     if sec["title"] or content:
    #         cleaned.append({"title": sec["title"], "content": content})
    # return cleaned, body_size


In [2]:
# sections, body_size = extract_sections_from_pdf("/home/janderson/Documentos/challenge-artificial-intelligence/data/Capítulo do Livro.pdf")
# for s in sections:
#     print("==", s["title"])
#     print(s["content"][:300], "...\n")

extract_sections_from_pdf("/home/janderson/Documentos/challenge-artificial-intelligence/data/Capítulo do Livro.pdf")


{'type': 0, 'number': 0, 'flags': 0, 'bbox': (65.58799743652344, 85.20597839355469, 391.5680236816406, 174.44996643066406), 'lines': [{'spans': [{'size': 36.0, 'flags': 20, 'bidi': 0, 'char_flags': 24, 'font': 'TitilliumWeb-SemiBold', 'color': 16777215, 'alpha': 255, 'ascender': 1.1009999513626099, 'descender': -0.30000001192092896, 'text': 'DESENVOLVIMENTO ', 'origin': (65.58799743652344, 124.84197998046875), 'bbox': (65.58799743652344, 85.20597839355469, 391.5680236816406, 135.64198303222656)}], 'wmode': 0, 'dir': (1.0, 0.0), 'bbox': (65.58799743652344, 85.20597839355469, 391.5680236816406, 135.64198303222656)}, {'spans': [{'size': 36.0, 'flags': 20, 'bidi': 0, 'char_flags': 24, 'font': 'TitilliumWeb-SemiBold', 'color': 16777215, 'alpha': 255, 'ascender': 1.1009999513626099, 'descender': -0.30000001192092896, 'text': 'DE SISTEMAS PHP ', 'origin': (65.58799743652344, 163.64996337890625), 'bbox': (65.58799743652344, 124.01396179199219, 358.5560607910156, 174.44996643066406)}], 'wmode':

In [4]:
from collections import Counter
from typing import List
import fitz  # PyMuPDF
from langchain.schema import Document

BLACK_FONT = "MyriadPro-Black"
SEMIBOLD_FONT = "MyriadPro-Semibold"

def _dominant_font(spanList):
    """
    Retorna a fonte dominante (mais frequente) dentre os spans com texto.
    """
    fonts = []
    for span in spanList:
        text = span.get("text", "").strip()
        if text:
            fonts.append(span.get("font", ""))
    if not fonts:
        return ""
    return Counter(fonts).most_common(1)[0][0]      

def _iter_lines(doc):
    """
    Itera todas as linhas do PDF na ordem de leitura,
    retornando tuplas (text, font).
    """
    for page in doc:
        data = page.get_text("dict")
        for block in data.get("blocks", []):
            if "lines" not in block:
                continue
            for line in block["lines"]:
                spansList = line.get("spans", [])
                text = ""
                for span in spansList:
                    text += span.get("text", "")
                text = text.strip()
                if not text:
                    continue
                font = _dominant_font(spansList)
                yield text, font

def _is_black(font: str) -> bool:
    return font and BLACK_FONT.lower() in font.lower()

def _is_semibold(font: str) -> bool:
    return font and SEMIBOLD_FONT.lower() in font.lower()

def extract_sections_as_documents(pdf_path: str) -> List[Document]:
    """
    Divide o PDF em seções:
      - Seção começa em linha(s) com fonte MyriadPro-Black (título pode ter várias linhas seguidas).
      - Conteúdo vai até a próxima ocorrência de título (MyriadPro-Black) ou fim.
      - Keywords = subseções (MyriadPro-Semibold) encontradas dentro da seção + o próprio título.
    Retorna uma lista de langchain.schema.Document.
    """
    doc = fitz.open(pdf_path)
    lines = list(_iter_lines(doc))
    i = 0
    number_of_lines = len(lines)
    docs: List[Document] = []

    while i < number_of_lines:
        text, font = lines[i]
 
        # Procurar início de seção pelo título em Black
        if _is_black(font):
            # 1) Agregar todas as linhas consecutivas em Black como parte do título
            title_parts = [text]
            j = i + 1
            while j < number_of_lines and _is_black(lines[j][1]):
                title_parts.append(lines[j][0])
                j += 1
            title = " ".join(part.strip() for part in title_parts).strip()

            # 2) Avançar para o conteúdo até o próximo título Black
            content_lines = []
            keywords = set()
            keywords.add(title)  # incluir o título como keyword

            k = j
            while k < number_of_lines and not _is_black(lines[k][1]):
                line_text, line_font = lines[k]
                # Coleta subseções como keywords (linhas em Semibold)
                if _is_semibold(line_font):
                    keywords.add(line_text.strip())
                content_lines.append(line_text)
                k += 1

            section_text = title + "\n\n" + "\n".join(content_lines).strip()
            docs.append(
                Document(
                    page_content=section_text,
                    metadata={
                        "source": pdf_path,
                        "title": title,
                        "keywords": sorted(list(keywords)),
                    },
                )
            )
            i = k  # continuar da próxima seção
        else:
            # linha fora de qualquer seção (antes do primeiro título) — opcionalmente ignore
            i += 1

    doc.close()
    return docs



/home/janderson/Documentos/challenge-artificial-intelligence/educacao/lib/python3.10/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [5]:
docs = extract_sections_as_documents("/home/janderson/Documentos/challenge-artificial-intelligence/data/Capítulo do Livro.pdf")

print(len(docs), "seções")
print(docs[0].metadata)       # {'source': '...', 'section_title': '...', 'keywords': [...], 'pages': [...]}
print(docs[1].metadata)       # {'source': '...', 'section_title': '...', 'keywords': [...], 'pages': [...]}
print(docs[2].metadata)       # {'source': '...', 'section_title': '...', 'keywords': [...], 'pages': [...]}
print(docs[3].metadata)       # {'source': '...', 'section_title': '...', 'keywords': [...], 'pages': [...]}
print(docs[4].metadata)       # {'source': '...', 'section_title': '...', 'keywords': [...], 'pages': [...]}
# print(docs[7].page_content[:500], "...")


5 seções
{'source': '/home/janderson/Documentos/challenge-artificial-intelligence/data/Capítulo do Livro.pdf', 'title': 'Criação de páginas web com HTML5 Objetivos de aprendizagem', 'keywords': ['Criação de páginas web com HTML5 Objetivos de aprendizagem']}
{'source': '/home/janderson/Documentos/challenge-artificial-intelligence/data/Capítulo do Livro.pdf', 'title': 'Introdução', 'keywords': ['Introdução']}
{'source': '/home/janderson/Documentos/challenge-artificial-intelligence/data/Capítulo do Livro.pdf', 'title': 'Estrutura de uma página web com HTML5', 'keywords': ['Article', 'Body', 'Doctype', 'Estrutura de uma página web com HTML5', 'Figura 1. Estrutura básica de uma página HTML5.', 'Head', 'Header e footer', 'Html', 'Nav e aside', 'Principais elementos da estrutura de uma página HTML5', 'Section', 'Title', 'https://goo.gl/VHQ5n']}
{'source': '/home/janderson/Documentos/challenge-artificial-intelligence/data/Capítulo do Livro.pdf', 'title': 'Formatação de texto de uma página web 

In [9]:
print(docs[3])

page_content='Formatação de texto de uma página web com HTML5

A especificação HTML5 disponibiliza uma série de elementos para formatar
textos e criar links e âncoras em páginas web. Para realizar isso você deve
usar tags específicas que permitem formatar os elementos de forma padrão,
visando equilibrar o código com a semântica do HTML5.
5
Criação de páginas web com HTML5
Formatação de texto
Uma página web exibe seu conteúdo texto diferente da forma como é es­
crito no código-fonte HTML. Essa diferença se dá porque seu conteúdo
requer marcações específicas nos objetos para realizar a formatação, ou
seja, é preciso que você insira tags para definir a forma como os textos
são apresentados.
Parágrafo
O elemento <p> indica a marcação de um parágrafo no texto, inserindo,
automaticamente, uma quebra de linha ao final quando localiza a tag </p>,
que indica o fechamento do parágrafo. Sem esses elementos, qualquer texto
em uma página HTML será escrito em sequência, mesmo que você insira
quebras

In [10]:
from langchain.document_loaders import PyPDFLoader, DirectoryLoader
from langchain.text_splitter import RecursiveCharacterTextSplitter

In [4]:
def load_pdf_files(data):
    loader = DirectoryLoader(
        data, 
        glob="*.pdf",
        loader_cls=PyPDFLoader
    )
    documents = loader.load()
    return documents

In [5]:
extracted_data = load_pdf_files('data')

In [6]:
extracted_data

[Document(metadata={'producer': 'Adobe PDF library 15.00', 'creator': 'Adobe Illustrator CC 2017 (Macintosh)', 'creationdate': '2017-10-31T14:11:59-02:00', 'creatorversion': '21.0.0', 'moddate': '2020-02-12T15:09:43-03:00', 'title': 'Capítulo do Livro', 'source': 'data/Capítulo do Livro.pdf', 'total_pages': 20, 'page': 0, 'page_label': '1'}, page_content='DESENVOLVIMENTO \nDE SISTEMAS PHP \nMaurício de Oliveira Saraiva'),
 Document(metadata={'producer': 'Adobe PDF library 15.00', 'creator': 'Adobe Illustrator CC 2017 (Macintosh)', 'creationdate': '2017-10-31T14:11:59-02:00', 'creatorversion': '21.0.0', 'moddate': '2020-02-12T15:09:43-03:00', 'title': 'Capítulo do Livro', 'source': 'data/Capítulo do Livro.pdf', 'total_pages': 20, 'page': 1, 'page_label': '2'}, page_content='Criação de páginas web \ncom HTML5\nObjetivos de aprendizagem\nAo final deste texto, você deve apresentar os seguintes aprendizados:\n \x84 Definir a estrutura de uma página web com HTML5.\n \x84 Aplicar a formatação

In [7]:
len(extracted_data)

20

In [8]:
from typing import List
from langchain.schema import Document

def filter_to_minimal_docs(docs: List[Document]) ->List[Document]:
    minimal_docs: List[Document] = []
    for doc in docs:
        src = doc.metadata.get("source")
        minimal_docs.append(
            Document(
                page_content=doc.page_content,
                metadata={"source": src}
            )
        )
    return minimal_docs


In [9]:
minimal_docs = filter_to_minimal_docs(extracted_data)

In [10]:
minimal_docs

[Document(metadata={'source': 'data/Capítulo do Livro.pdf'}, page_content='DESENVOLVIMENTO \nDE SISTEMAS PHP \nMaurício de Oliveira Saraiva'),
 Document(metadata={'source': 'data/Capítulo do Livro.pdf'}, page_content='Criação de páginas web \ncom HTML5\nObjetivos de aprendizagem\nAo final deste texto, você deve apresentar os seguintes aprendizados:\n \x84 Definir a estrutura de uma página web com HTML5.\n \x84 Aplicar a formatação de texto em uma página web com HTML5.\n \x84 Desenvolver listas e tabelas em uma página web com HTML5.\nIntrodução\nSistemas desenvolvidos para a plataforma web, tanto para páginas es -\ntáticas como dinâmicas, utilizam a linguagem HTML para a exibição \ndo conteúdo. Com HTML5, é possível criar páginas web com diversos \nrecursos para a apresentação de dados, por meio de novas marcações \nque permitem o uso de semântica e acessibilidade. Isso facilita a pesquisa \npor motores de busca automática, dispositivos próprios para deficientes \nvisuais e auditivos, e

In [11]:
#dividir documentos em chunks
def text_split(minimal_docs):
    text_splitter = RecursiveCharacterTextSplitter(
        chunk_size=500,
        chunk_overlap=20,
    )
    text_chunk = text_splitter.split_documents(minimal_docs)
    return text_chunk

In [14]:
text_chunk = text_split(minimal_docs)
print(f"Number of text chunks: {len(text_chunk)}")

Number of text chunks: 50


In [15]:
text_chunk

[Document(metadata={'source': 'data/Capítulo do Livro.pdf'}, page_content='DESENVOLVIMENTO \nDE SISTEMAS PHP \nMaurício de Oliveira Saraiva'),
 Document(metadata={'source': 'data/Capítulo do Livro.pdf'}, page_content='Criação de páginas web \ncom HTML5\nObjetivos de aprendizagem\nAo final deste texto, você deve apresentar os seguintes aprendizados:\n \x84 Definir a estrutura de uma página web com HTML5.\n \x84 Aplicar a formatação de texto em uma página web com HTML5.\n \x84 Desenvolver listas e tabelas em uma página web com HTML5.\nIntrodução\nSistemas desenvolvidos para a plataforma web, tanto para páginas es -\ntáticas como dinâmicas, utilizam a linguagem HTML para a exibição'),
 Document(metadata={'source': 'data/Capítulo do Livro.pdf'}, page_content='do conteúdo. Com HTML5, é possível criar páginas web com diversos \nrecursos para a apresentação de dados, por meio de novas marcações \nque permitem o uso de semântica e acessibilidade. Isso facilita a pesquisa \npor motores de busca

In [11]:
from langchain.embeddings import HuggingFaceEmbeddings

def downloald_hugging_faace_embeddings():
    model_name = "BAAI/bge-small-en-v1.5"
    embeddings = HuggingFaceEmbeddings(model_name=model_name, model_kwargs={"device": "cpu"})
    return embeddings


embedding = downloald_hugging_faace_embeddings()


/tmp/ipykernel_7501/424247799.py:5: LangChainDeprecationWarning: The class `HuggingFaceEmbeddings` was deprecated in LangChain 0.2.2 and will be removed in 1.0. An updated version of the class exists in the :class:`~langchain-huggingface package and should be used instead. To use it run `pip install -U :class:`~langchain-huggingface` and import as `from :class:`~langchain_huggingface import HuggingFaceEmbeddings``.
  embeddings = HuggingFaceEmbeddings(model_name=model_name, model_kwargs={"device": "cpu"})


In [12]:
vector = embedding.embed_query("Hello world")
vector

[0.01519613154232502,
 -0.022570662200450897,
 0.008547082543373108,
 -0.07417060434818268,
 0.003836424555629492,
 0.0027135657146573067,
 -0.03126790374517441,
 0.04463401064276695,
 0.04405517131090164,
 -0.007871180772781372,
 -0.025200815871357918,
 -0.033366575837135315,
 0.014427902176976204,
 0.04653819277882576,
 0.008555065840482712,
 -0.01614576019346714,
 0.0074058398604393005,
 -0.019012469798326492,
 -0.11472626030445099,
 -0.018157577142119408,
 0.12635937333106995,
 0.029702914878726006,
 0.025281012058258057,
 -0.03421789035201073,
 -0.04099970683455467,
 0.006617303937673569,
 0.010270675644278526,
 0.022362256422638893,
 0.004436364397406578,
 -0.1273096203804016,
 -0.016149284318089485,
 -0.020380139350891113,
 0.04721219092607498,
 0.011579902842640877,
 0.0681871548295021,
 0.007298648823052645,
 -0.0178530216217041,
 0.0407821349799633,
 -0.01026944350451231,
 0.023757033050060272,
 0.010602838359773159,
 -0.02858441136777401,
 0.008159711956977844,
 -0.015180503

In [13]:
print(len(vector)) 

384


In [14]:
from dotenv import load_dotenv
import os
load_dotenv()

True

In [15]:
PINECONE_API_KEY = os.getenv("PINECONE_API_KEY")
OPENAI_API_KEY = os.getenv("OPENAI_API_KEY")

os.environ["PINECONE_API_KEY"] = PINECONE_API_KEY
os.environ["OPENAI_API_KEY"] = OPENAI_API_KEY


In [16]:
from pinecone import Pinecone
pinecone_api_key = PINECONE_API_KEY

pc = Pinecone(api_key=pinecone_api_key)
pc

In [17]:
from pinecone import ServerlessSpec
index_name = "chatbot"

if  not pc.has_index(index_name): 
    pc.create_index(
        name=index_name,
        dimension=384,
        metric="cosine",
        spec=ServerlessSpec(cloud="aws", region="us-east-1")
    )

index = pc.Index(index_name)
     

In [18]:
from langchain_pinecone import PineconeVectorStore

docsearch = PineconeVectorStore.from_documents(
    documents=docs,
    embedding=embedding,
    index_name=index_name, 
)

In [64]:
docsearch = PineconeVectorStore.from_existing_index(
    index_name=index_name,
    embedding=embedding
)

In [65]:
#Adicionar mais dados
dswith = Document(
    page_content="New document content to be added.",
    metadata={"source": "teste"}
)

In [66]:
docsearch.add_documents(documents=[dswith])

['de7be206-0e54-44c7-8ca6-22dd8a29d339']

In [67]:
retriever = docsearch.as_retriever(search_type="similarity", search_kwargs={"k": 3})


In [68]:
retriever_docs = retriever.invoke("Quais os principais elementos da estrutura de uma página HTML5?")
retriever_docs

[Document(id='dadbceb8-c9d8-4e96-851e-6310ab776320', metadata={'source': 'data/Capítulo do Livro.pdf'}, page_content='Principais elementos da estrutura de uma página HTML5\nComo dito anteriormente, uma página HTML é composta por marcações. Essas \nmarcações estão inseridas no documento dentro de itens específicos chamados \nde tags, etiquetas ou elementos, que respeitam uma estrutura hierárquica bem \ndefinida. A Figura 1 apresenta essa estrutura.\nFigura 1. Estrutura básica de uma página HTML5.\nDoctype\nA instrução DOCTYPE, apresentada na linha 1, é um comando especial que'),
 Document(id='964f6082-eea4-4694-bd7e-fdc180bc55c3', metadata={'source': 'data/Capítulo do Livro.pdf'}, page_content='Principais elementos da estrutura de uma página HTML5\nComo dito anteriormente, uma página HTML é composta por marcações. Essas \nmarcações estão inseridas no documento dentro de itens específicos chamados \nde tags, etiquetas ou elementos, que respeitam uma estrutura hierárquica bem \ndefinida. 

In [74]:
from langchain_openai import ChatOpenAI

chatModel = ChatOpenAI(model="gpt-4o")

In [75]:
from langchain.chains import create_retrieval_chain
from langchain.chains.combine_documents import create_stuff_documents_chain
from langchain_core.prompts import ChatPromptTemplate


In [76]:
system_promp = (
    "You are an assistant for question answering task"
    "Use the following context to answer the question."
    "If you don't know the answer, just say that you don't know, don't try to make up an answer."
    "keep the answer concise."
    "keep the answer short."
    "\n\n"
    "{context}"
)

prompt = ChatPromptTemplate.from_messages([
    ("system", system_promp),
    ("human", "{input}"),
])

In [77]:
question_answer_chain = create_stuff_documents_chain(chatModel,prompt)
rag_chain = create_retrieval_chain(retriever,question_answer_chain)


In [78]:
response = rag_chain.invoke({"input": "Quais os principais elementos da estrutura de uma página HTML5?"})
print(response["answer"])

Os principais elementos da estrutura de uma página HTML5 são as tags e a declaração DOCTYPE. As tags são usadas para definir a estrutura e o conteúdo, enquanto a declaração DOCTYPE especifica a versão do HTML utilizada.
